In [17]:
import os
import yt_dlp
import shutil
import ffmpeg
from IPython.display import HTML, display
from base64 import b64encode
from tqdm import tqdm
import time

In [25]:
def delete_folder(folder_path):
    if os.path.exists(folder_path) and os.path.isdir(folder_path):
        shutil.rmtree(folder_path)
        print(f"Deleted folder: {folder_path}")
    elif os.path.isfile(folder_path):
        os.remove(folder_path)
        print(f"Deleted file: {folder_path}")

In [26]:
def download_youtube_video(url, output_path='.'):
    ydl_opts = {
        'format': 'mp4',
        'outtmpl': f'{output_path}/{'input'}.%(ext)s'
    }
    
    with yt_dlp.YoutubeDL(ydl_opts) as ydl:
        ydl.download([url])
        print(f"Video downloaded successfully and saved to {output_path}")

    return 'input.mp4'

In [27]:
# def resize_video(input_video_path, output_size):
#     resized_video_path = "resized_video.mp4"
#     process = (
#         ffmpeg
#         .input(input_video_path)
#         .filter('scale', output_size[1], output_size[0])
#         .output(resized_video_path)
#     )
#     process.run()
#     return resized_video_path

In [28]:
def apply_yolo_model(resized_video_path, yolo_model_path):
    yolo_command = f'yolo track model="runs/detect/train16/weights/best.pt" source="input.mp4" show=True'
    os.system(yolo_command)
    return "runs/detect/track/input.avi"

In [29]:
def convert_video_format(tracked_video_path):
    output_video_path = "output.mp4"
    ffmpeg_command = f'ffmpeg -i {tracked_video_path} -vf fps=15 -s 640x480 -vcodec libx264 {output_video_path}'
    os.system(ffmpeg_command)
    return output_video_path

In [30]:
def display_video(output_video_path):
    mp4 = open(output_video_path, 'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(mp4).decode()

    html_video = HTML(f"""
    <video controls>
          <source src="{data_url}" type="video/mp4">
          Your browser does not support the video tag.
    </video>
    """)
    display(html_video)

In [33]:
def process_youtube_video(youtube_url, yolo_model_path, output_size=(384, 640)):
    # Delete the folder if it exists
    delete_folder('runs/detect/track')
    delete_folder('input.mp4')
    delete_folder('output.mp4')
    
    
    # Download the YouTube video
    print("Downloading YouTube video...")
    input_video_path = download_youtube_video(youtube_url)
    
    # # Resize the video
    # print("Resizing video...")
    # resized_video_path = resize_video(input_video_path, output_size)
    
    # Apply YOLO model to the video
    print("Applying YOLO model...")
    tracked_video_path = apply_yolo_model(input_video_path, yolo_model_path)
    
    # Convert the tracked video to the desired format
    print("Converting video format...")
    output_video_path = convert_video_format(tracked_video_path)
    
    # Display the output video
    print("Displaying video...")
    display_video(output_video_path)
    print("Process complete.")

# Example usage
youtube_url = input("Enter Youtube Soccer Video URL:")
yolo_model_path = "runs/detect/train16/weights/best.pt"
process_youtube_video(youtube_url, yolo_model_path)

Enter Youtube Soccer Video URL: https://www.youtube.com/shorts/069UgGnwfF8


Deleted folder: runs/detect/track
Deleted file: input.mp4
Deleted file: output.mp4
[youtube] Extracting URL: https://www.youtube.com/shorts/069UgGnwfF8
[youtube] 069UgGnwfF8: Downloading webpage
[youtube] 069UgGnwfF8: Downloading ios player API JSON
[youtube] 069UgGnwfF8: Downloading m3u8 information
[info] 069UgGnwfF8: Downloading 1 format(s): 18
[download] Destination: input.mp4
[download] 100% of    2.14MiB in 00:00:00 at 4.85MiB/s   
Video downloaded successfully and saved to .
Applying YOLO model...
Converting video format...
Displaying video...


Process complete.
